### Note-  
### 1]use google colab 
### 2]Python version 3.10
### 3]Mount google drive which should have pdf folder in it or else give proper path to pdf folder
### 4]Only pdf file parser is used

### Import libraries required

In [5]:
import chromadb
import PyPDF2
import os
import re
from sentence_transformers import util, SentenceTransformer
from langchain.text_splitter import CharacterTextSplitter

### Initiate chromadb server

In [6]:
client = chromadb.Client()
collection = client.create_collection("kArmayogi_embeddings")

### Mount drive having pdf folder

In [7]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [8]:
import locale
locale.setlocale(locale.LC_ALL, 'en_US.UTF-8')
!pip install stanfordnlp

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 1.3 MB/s eta 0:00:00


In [9]:
# pip install fastcoref

In [10]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [11]:
pip install fastcoref

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 4.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 19.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 21.2 MB/s eta 0:00:00
  Created wheel for fastcoref: filename=fastcoref-2.1.6-py3-none-any.whl size=31252 sha256=c261a40f7356abb6b2e33e76618ef53b57a59d291022c604b90f05be11c9f191
  Stored in directory: /root/.cache/pip/wheels/73/ac/49/24d3e434b85513f46503fbea7e7eb6353e32b66619ea86b410
Successfully built fastcoref


In [14]:
import locale
locale.setlocale(locale.LC_ALL, 'en_US.UTF-8')


'en_US.UTF-8'

In [15]:
import locale
locale.setlocale(locale.LC_ALL, 'en_US.UTF-8')
!pip install stanfordnlp

In [16]:
!pip install stanfordnlp

In [17]:
pip install fastcoref

### Parsing pdf->creating chunks of size 500 and overlap of 100

In [22]:
from fastcoref import FCoref

class SimpleDocument:
    def __init__(self, page_content, metadata=None):
        self.page_content = page_content
        self.metadata = {} if metadata is None else metadata

file_data = []
folder_path ="/content/drive/MyDrive/pdf"

for file_name in os.listdir(folder_path):
    if file_name.endswith(".pdf"):
        file_path = os.path.join(folder_path, file_name)

        with open(file_path, 'rb') as pdf_file:
            pdf_reader = PyPDF2.PdfReader(pdf_file)
            for page in range(len(pdf_reader.pages)):
                text = pdf_reader.pages[page].extract_text()
                try:
                  document_splitter = CharacterTextSplitter(separator='  \n \n', chunk_size=500, chunk_overlap=100)
                  document_chunks = document_splitter.split_documents([SimpleDocument(text)])
                  print(document_chunks)



                except:
                  document_splitter = CharacterTextSplitter(separator='\n', chunk_size=500, chunk_overlap=100)
                  document_chunks = document_splitter.split_documents([SimpleDocument(text)])
                  print(document_chunks)
                  print("in except block")

                for i, document_chunk in enumerate(document_chunks):

                    document_chunk_text = re.sub(" \n", " ", document_chunk.page_content)
                    paragraph=document_chunk_text
                    model = FCoref(device='cuda:0')

                    preds = model.predict(
                      texts=[paragraph]
                    )

                    preds[0].get_clusters(as_strings=False)
                    clusters=preds[0].get_clusters()


                    for cluster in clusters:
                      for i in range (len(cluster)):
                        paragraph=paragraph.replace(cluster[i-1], cluster[0], 1)

                    enriched_document=paragraph
                    file_data.append({"file_name": f"{file_name}_{i}", "content": enriched_document})


[Document(page_content="IMMEDIATE\nNo.T-16017/6/2023-TFA .\nGovernment ofIndia\nMinistry ofPersonnel, Public Grievances and Pensions\nDepartment ofPersonnel &Training\n(Training Division)*****\nOld JNU Campus, New Delhi\nDated the 28^ July, 2023\nOFFICE MEMORANDUM\nSub: Karmayogi Guidelines, 2023.\nTh^ undersigned isdirected tosay that this Department isthe nodal\nagency ofGovernment ofIndia formatters related totraining ofCivil Servants.\nThe Civil Services play acentral role ingovernance and itsdelivery of\npublic services. Toequip the civil services with the right attitudes, skills,\nknowledge and competencies aligned tothe demands and expectations ofa\nrapidly growing economy and itsaspirational citizens, Government of India\nlaunched the National Programme for Civil Services Capacity Building\n(NPCSCB) -Mission Karmayogi. The Mission Karmayogi aims atdeveloping a\ncitizen-centric and future-ready civil service and through democratized and\ncompetency-led capacity building, which e

config.json:   0%|          | 0.00/819 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/393 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/798k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

...

[Document(page_content='Onboarding in a Box for department s  \nFor detailed understanding of the FRACing exercise, please refer to the  Draft document for “The \nFramework of Roles, Activities and Competencies”.   \n8.7 Onboarding Associated CTIs  \nEach department can onboard their associated CTI(s) on iGOT  KY both as Users and Content Providers. \nDetailed step by step guide for Onboarding CTIs will be provided later.'), Document(page_content='9. Key Contacts at iGOT  KY Team  \nIn case of any queries, the department can reach out to  \n• Mr. Manoj Gupta (US, Training Division, DoPT) at manoj.gupta74@nic.in  \n• Ms. G. D. Jayanthi (DS, Training Division, DoPT) at g.d.jayanthi@nic.in  \n• Dr. Kartik Hegadekatti (DS, Training Division) at  kartik.hegadekatti@nic.in   \n \n \n10.  Annexures  \n10.1 Annexure A – iGOT KY User Manual')]


Map:   0%|          | 0/1 [00:00<?, ? examples/s]

Inference:   0%|          | 0/1 [00:00<?, ?it/s]

Map:   0%|          | 0/1 [00:00<?, ? examples/s]

Inference:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
# fast coref applied at the end of chunking document

In [24]:
import torch
print(torch.cuda.is_available())


True


In [ ]:
# file_data

### ->creating embedding vectors for chuncks

In [32]:
from sentence_transformers import SentenceTransformer

emb_model = SentenceTransformer('paraphrase-MiniLM-L3-v2')

documents = []
embeddings = []
metadatas = []
ids = []

for index, data in enumerate(file_data):
    documents.append(data['content'])

    embedding = emb_model.encode(data['content']).tolist()
    embeddings.append(embedding)
    metadatas.append({'source': data['file_name']})
    ids.append(str(index + 1))
    # print(embedding)

print(documents)

["IMMEDIATE\nNo.T-16017/6/2023-TFA .\nGovernment ofIndia\nMinistry ofPersonnel, Public Grievances and Pensions\nDepartment ofPersonnel &Training\n(Training Division)*****\nOld JNU Campus, New Delhi\nDated the 28^ July, 2023\nOFFICE MEMORANDUM\nSub: Karmayogi Guidelines, 2023.\nTh^ undersigned isdirected tosay that this Department isthe nodal\nagency Government ofIndia formatters related totraining ofCivil Servants.\nThe Civil Services play acentral role ingovernance and itsdelivery of\npublic services. Toequip The Civil Services with the right attitudes, skills,\nknowledge and competencies aligned tothe demands and expectations ofa\nrapidly growing economy and itsaspirational citizens, Government ofIndia\nlaunched the National Programme for Civil Services Capacity Building\n(NPCSCB) -Mission Karmayogi. the National Programme for Civil Services Capacity Building\n(NPCSCB) -Mission Karmayogi aims atdeveloping a\ncitizen-centric and future-ready civil service and through democratized and\

### Create new karmayogicollection_emb collection 

In [33]:
karmayogicollection_emb = client.create_collection("karmayogicollection_emb")



karmayogicollection_emb.add(
    documents=documents,
    embeddings=embeddings,
    metadatas=metadatas,
    ids=ids
)


### Converting queries into vectors and utilizing an embedding collection retrieval mechanism to identify the top 4 paragraphs containing relevant answers.

In [41]:

model = SentenceTransformer('paraphrase-MiniLM-L3-v2')
query = "What is mandetory part of Cadre training part?"
input_em = emb_model.encode(query).tolist()

results = karmayogicollection_emb.query(
    query_embeddings=[input_em],
    n_results=4
)


for answer in (results['documents'][0]):
  print(answer)
  print("*****************************************")


Forallnon-cadre /service specific resources, including temporary hires, etc., there shall be
acomponent ofatleastone-week onsite Induction Training tobeanchored byCSTIs which
willbespecifically identified forthepurpose. This willbeinaddition tomandatory online
Induction modules notified byDOPT ortheMDOs from time totime.V.
Develop amandatory immersion programme (know your ministry) forallnew inductees
aswell asinstitutionalize programmes which take place regularly throughout theCSTIsear for
thebenefit ofallemployees.VI.
Provide mentoring support intheir training andcapacity building plans tomentor in-
service officers.Vll.
Collaboration: Develop training collaborations independently orthrough CSTIs
preferably onreciprocal basis with global anddomestic partners forboth onsite andonline
delivery ofcourses andmodules, sharing oflearning resources andbest practices. These
training interventions may beshort-term/long-term, inspecialized domain andfunctional
areas, toaddress thecompetencies 